In [3]:
import random
import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F
import pickle
import random
import numpy as np
from nltk.util import ngrams
from sys import platform

# To make sure the folder standards work in windows and other systems
if platform == "win32":
    # Windows...
    folder_separator = "\\"
else:
    folder_separator = "/"

    
MAX_LENGTH = 16 # This depends on the length of sentences in our sample set..
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

To represent our words as vectors, we use one-hot encoding. Each word is then a large vector full of zeroes, with a one in the position of the word. The size of the vector is the length of the vocabulary. The following helper class creates a Lang object, which is useful for making our one-hot encoded word vectors. The Lang object contains two dictionaries: a word2index dictionary that has each word of our vocabulary as keys, and its index in the vector as value. The other dictionary is index2word, which does the same but is reversed. It also keeps track of how many words we have, in a word2count dictionary.

In [4]:
SOS_token = 0
EOS_token = 1


class Lang:
    def __init__(self, name):
        self.name = name
        self.word2index = {}
        self.word2count = {}
        self.index2word = {0: "SOS", 1: "EOS"}
        self.n_words = 2  # Count SOS and EOS

    def addSentence(self, sentence):
        for word in sentence.split(' '):
            self.addWord(word)

    def addWord(self, word):
        if word not in self.word2index:
            self.word2index[word] = self.n_words
            self.word2count[word] = 1
            self.index2word[self.n_words] = word
            self.n_words += 1
        else:
            self.word2count[word] += 1

We then make two Lang classes from our dataset. The Lang class stores useful information about the words and indexes in our one-hot encoded vector. We use these classes for training. The input language is going to be English, and the output language will be Dutch. Also, in this step each input sentence is reversed.

In [5]:
def lang_class_maker(data, lang1, lang2):
    input_lang = Lang(lang1)
    output_lang = Lang(lang2)
    
    for pair in data:
        # The sentence is splitted, reversed, and reassembled
        input_sentence = " ".join(pair[0].split()[::-1])
        input_lang.addSentence(input_sentence)
        output_lang.addSentence(pair[1])
        
    return input_lang, output_lang

def lang_class_updater(data, input_lang, output_lang):
    for pair in data:
        # The sentence is splitted, reversed, and reassembled
        input_sentence = " ".join(pair[0].split()[::-1])
        input_lang.addSentence(input_sentence)
        output_lang.addSentence(pair[1])
        
    return input_lang, output_lang

Below follow the encoder, decoder and attention decoder classes, as described by the [Pytorch tutorial](https://pytorch.org/tutorials/intermediate/seq2seq_translation_tutorial.html).

In [6]:
class EncoderRNN(nn.Module):
    def __init__(self, input_size, hidden_size):
        super(EncoderRNN, self).__init__()
        self.hidden_size = hidden_size

        self.embedding = nn.Embedding(input_size, hidden_size)
        self.gru = nn.GRU(hidden_size, hidden_size)

    def forward(self, input, hidden):
        embedded = self.embedding(input).view(1, 1, -1)
        output = embedded
        output, hidden = self.gru(output, hidden)
        return output, hidden

    def initHidden(self):
        return torch.zeros(1, 1, self.hidden_size, device=device)

In [7]:
class DecoderRNN(nn.Module):
    def __init__(self, hidden_size, output_size):
        super(DecoderRNN, self).__init__()
        self.hidden_size = hidden_size

        self.embedding = nn.Embedding(output_size, hidden_size)
        self.gru = nn.GRU(hidden_size, hidden_size)
        self.out = nn.Linear(hidden_size, output_size)
        self.softmax = nn.LogSoftmax(dim=1)

    def forward(self, input, hidden):
        output = self.embedding(input).view(1, 1, -1)
        output = F.relu(output)
        output, hidden = self.gru(output, hidden)
        output = self.softmax(self.out(output[0]))
        return output, hidden

    def initHidden(self):
        return torch.zeros(1, 1, self.hidden_size, device=device)

In [8]:
class AttnDecoderRNN(nn.Module):
    def __init__(self, hidden_size, output_size, dropout_p=0.1, max_length=MAX_LENGTH):
        super(AttnDecoderRNN, self).__init__()
        self.hidden_size = hidden_size
        self.output_size = output_size
        self.dropout_p = dropout_p
        self.max_length = max_length

        self.embedding = nn.Embedding(self.output_size, self.hidden_size)
        self.attn = nn.Linear(self.hidden_size * 2, self.max_length)
        self.attn_combine = nn.Linear(self.hidden_size * 2, self.hidden_size)
        self.dropout = nn.Dropout(self.dropout_p)
        self.gru = nn.GRU(self.hidden_size, self.hidden_size)
        self.out = nn.Linear(self.hidden_size, self.output_size)

    def forward(self, input, hidden, encoder_outputs):
        embedded = self.embedding(input).view(1, 1, -1)
        embedded = self.dropout(embedded)

        attn_weights = F.softmax(
            self.attn(torch.cat((embedded[0], hidden[0]), 1)), dim=1)
        attn_applied = torch.bmm(attn_weights.unsqueeze(0),
                                 encoder_outputs.unsqueeze(0))

        output = torch.cat((embedded[0], attn_applied[0]), 1)
        output = self.attn_combine(output).unsqueeze(0)

        output = F.relu(output)
        output, hidden = self.gru(output, hidden)

        output = F.log_softmax(self.out(output[0]), dim=1)
        return output, hidden, attn_weights

    def initHidden(self):
        return torch.zeros(1, 1, self.hidden_size, device=device)

We need the following helper functions for our training. When given a pair of sentences, we want to make two tensors from them, containing the indexes of each word in the sentence.

In [9]:
def indexesFromSentence(lang, sentence):
    total = list()
    for word in sentence.split(" "):
        try:
            total.append(lang.word2index[word])
        except:
            print(f"This is the word: {word}")
            raise Exception("We fucked up, and its a key error")
    return total


def tensorFromSentence(lang, sentence):
    indexes = indexesFromSentence(lang, sentence)
    indexes.append(EOS_token)
    return torch.tensor(indexes, dtype=torch.long, device=device).view(-1, 1)


def tensorsFromPair(pair):
    input_tensor = tensorFromSentence(input_lang, pair[0])
    target_tensor = tensorFromSentence(output_lang, pair[1])
    return (input_tensor, target_tensor)

The following two functions are very useful for the human operator at the computer. The first one shows a plot with the cost per amount of iterations, which helps with determining how fast the model improves, and gives an indication of how many iterations we should use. The second one calculates the amount of time that went by, and the amount of time left until the training is completed.

In [10]:
import matplotlib.pyplot as plt
plt.switch_backend('agg')
import matplotlib.ticker as ticker
import numpy as np


def showPlot(points):
    plt.figure()
    fig, ax = plt.subplots()
    # this locator puts ticks at regular intervals
    loc = ticker.MultipleLocator(base=0.2)
    ax.yaxis.set_major_locator(loc)
    plt.plot(points)

In [11]:
import time
import math


def asMinutes(s):
    m = math.floor(s / 60)
    s -= m * 60
    return '%dm %ds' % (m, s)


def timeSince(since, percent):
    now = time.time()
    s = now - since
    es = s / (percent)
    rs = es - s
    return '%s (- %s)' % (asMinutes(s), asMinutes(rs))

Now we are finally ready for training, which we will do with the following two functions. The first one trains for one sentence pair. The second one iterates a certain amount of times, and trains one pair of sentences in each iteration.

In [12]:
def train(input_tensor, target_tensor, encoder, decoder, encoder_optimizer, decoder_optimizer, criterion, max_length=MAX_LENGTH):
    encoder_hidden = encoder.initHidden()

    encoder_optimizer.zero_grad()
    decoder_optimizer.zero_grad()

    input_length = input_tensor.size(0)
    target_length = target_tensor.size(0)

    encoder_outputs = torch.zeros(max_length, encoder.hidden_size, device=device)

    loss = 0
    for ei in range(input_length):
        encoder_output, encoder_hidden = encoder(
            input_tensor[ei], encoder_hidden)
        encoder_outputs[ei] = encoder_output[0, 0]

    decoder_input = torch.tensor([[SOS_token]], device=device)

    decoder_hidden = encoder_hidden
    
    # Use its own predictions as the next input
    for di in range(target_length):
            decoder_output, decoder_hidden = decoder(
                decoder_input, decoder_hidden)
            topv, topi = decoder_output.topk(1)
            decoder_input = topi.squeeze().detach()  # detach from history as input

            loss += criterion(decoder_output, target_tensor[di])
            if decoder_input.item() == EOS_token:
                break

    loss.backward()

    encoder_optimizer.step()
    decoder_optimizer.step()

    return loss.item() / target_length

Here we can put the different tweaks to the models. The first one is to use teacher forcing. This basically uses the target sentence (given from the data) as input in the Recurrent Neural Network, so the model already knows the target sentence and tries to approximate this. The teacher forcing ratio can be specified in the input, and is a number between 0 and 1, indicating in how much of the cases we will apply teacher forcing.

In [13]:
def train_teacher(input_tensor, target_tensor, encoder, decoder, encoder_optimizer, decoder_optimizer, criterion, 
                  max_length=MAX_LENGTH, teacher_forcing_ratio=0.5):
    encoder_hidden = encoder.initHidden()

    encoder_optimizer.zero_grad()
    decoder_optimizer.zero_grad()

    input_length = input_tensor.size(0)
    target_length = target_tensor.size(0)

    encoder_outputs = torch.zeros(max_length, encoder.hidden_size, device=device)

    loss = 0

    for ei in range(input_length):
        encoder_output, encoder_hidden = encoder(
            input_tensor[ei], encoder_hidden)
        encoder_outputs[ei] = encoder_output[0, 0]

    decoder_input = torch.tensor([[SOS_token]], device=device)

    decoder_hidden = encoder_hidden

    use_teacher_forcing = True if random.random() < teacher_forcing_ratio else False

    if use_teacher_forcing:
        # Teacher forcing: Feed the target as the next input
        for di in range(target_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden, encoder_outputs)
            loss += criterion(decoder_output, target_tensor[di])
            decoder_input = target_tensor[di]  # Teacher forcing

    else:
        # Without teacher forcing: use its own predictions as the next input
        for di in range(target_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden, encoder_outputs)
            topv, topi = decoder_output.topk(1)
            decoder_input = topi.squeeze().detach()  # detach from history as input

            loss += criterion(decoder_output, target_tensor[di])
            if decoder_input.item() == EOS_token:
                break

    loss.backward()

    encoder_optimizer.step()
    decoder_optimizer.step()

    return loss.item() / target_length

In [14]:
def trainIters(encoder, decoder, pairs, n_iters, print_every=1000, plot_every=100, learning_rate=0.01):
    start = time.time()
    plot_losses = []
    print_loss_total = 0  # Reset every print_every
    plot_loss_total = 0  # Reset every plot_every

    encoder_optimizer = optim.SGD(encoder.parameters(), lr=learning_rate)
    decoder_optimizer = optim.SGD(decoder.parameters(), lr=learning_rate)
    training_pairs = [tensorsFromPair(pairs[i]) for i in range(n_iters)]
    criterion = nn.NLLLoss()

    for iter in range(1, n_iters + 1):
        training_pair = training_pairs[iter - 1]
        input_tensor = training_pair[0]
        target_tensor = training_pair[1]

        loss = train_teacher(input_tensor, target_tensor, encoder,
                     decoder, encoder_optimizer, decoder_optimizer, criterion)
        print_loss_total += loss
        plot_loss_total += loss

        if iter % print_every == 0:
            print_loss_avg = print_loss_total / print_every
            print_loss_total = 0
            print('%s (%d %d%%) %.4f' % (timeSince(start, iter / n_iters),
                                         iter, iter / n_iters * 100, print_loss_avg))

        if iter % plot_every == 0:
            plot_loss_avg = plot_loss_total / plot_every
            plot_losses.append(plot_loss_avg)
            plot_loss_total = 0

    showPlot(plot_losses)

After the model has been trained, we also want to be able to test what it's output is. The following function takes the trained encoder and decoder, and an English sentence as input, and produces a Dutch translation as output.

In [15]:
def evaluate(encoder, decoder, sentence, max_length=MAX_LENGTH):
    with torch.no_grad():
        input_tensor = tensorFromSentence(input_lang, sentence)
        input_length = input_tensor.size()[0]
        encoder_hidden = encoder.initHidden()

        encoder_outputs = torch.zeros(max_length, encoder.hidden_size, device=device)

        for ei in range(input_length):
            encoder_output, encoder_hidden = encoder(input_tensor[ei],
                                                     encoder_hidden)
            encoder_outputs[ei] += encoder_output[0, 0]

        decoder_input = torch.tensor([[SOS_token]], device=device)  # SOS

        decoder_hidden = encoder_hidden

        decoded_words = []

        for di in range(max_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden, encoder_outputs)
            topv, topi = decoder_output.data.topk(1)
            if topi.item() == EOS_token:
                decoded_words.append('<EOS>')
                break
            else:
                decoded_words.append(output_lang.index2word[topi.item()])

            decoder_input = topi.squeeze().detach()

        return decoded_words

In [16]:
def bleu_text(target_text: list, reference_text: list, n_precision = 4, smoothing = 0):
    """takes a target_text, and a reference_text, of the same length, as lists within lists, where each inner list is a
    tokenized sentence, n_precision, which determines up to which n-gram the bleu value is computed, and a possible
    smoothing"""
    temp = np.zeros((n_precision, 2)) #each row is an n(-gram), column 0 is counted matches, column 1 is total n-grams
    for i in range(0, len(target_text)):
        for j in range(0, n_precision):
            count = 0
            target = list(ngrams(target_text[i], j+1))
            reference = list(ngrams(reference_text[i], j+1))
            for x in target:
                #to make sure no n-gram is used as a match twice, it is removed from the reference list
                if x in reference:
                    reference.remove(x)
                    count += 1
            #if a smoothing is specified, and for a certain n-gram 0 counts were found, it is smoothed over
            if smoothing != 0 and count == 0:
                count = smoothing
            temp[j] += [count, len(target)]
    #the amount of matches will be divided by the total amount of n-grams
    result = temp[:,0]/temp[:,1]
    #the final result will be the geometric mean of the different n-gram results
    return result.prod()**(1/len(result))

In [19]:
# This initializes the encoder and the attention decoder. We can choose to specify the amount of hidden layers
hidden_size = 256
lang_chunk_num = 53542
initialized = False
pickle_off = f"data{folder_separator}final_sample.pkl"
file_stream = (open(pickle_off, "rb"))

while lang_chunk_num:
    try:
        print("Preparing Lang class...")
        pairs = pickle.load(file_stream)
        if initialized:
            input_lang, output_lang = lang_class_updater(pairs, input_lang, output_lang)
            print(f'{(1-(lang_chunk_num/53542)) *100} % vocabulary building is done')
        else:
            input_lang, output_lang = lang_class_maker(pairs, 'en', 'nl')
            initialized = True
    except EOFError:
        raise Exception("You have reached the end of chunks")
    lang_chunk_num -= 1


print(f"Input size: {input_lang.n_words}\nOutput size: {output_lang.n_words}")
file_stream.close()
file_stream = (open(pickle_off, "rb"))
initialized = False
print("En/De coding...")
encoder1 = EncoderRNN(input_lang.n_words, hidden_size).to(device)
attndecoder1 = AttnDecoderRNN(hidden_size, output_lang.n_words).to(device)



Preparing Lang class...
Preparing Lang class...
0.0018676926525018622 % vocabulary building is done
Preparing Lang class...
0.0037353853049926222 % vocabulary building is done
Preparing Lang class...
0.0056030779574944845 % vocabulary building is done
Preparing Lang class...
0.0074707706099852444 % vocabulary building is done
Preparing Lang class...
0.009338463262487107 % vocabulary building is done
Preparing Lang class...
0.011206155914977867 % vocabulary building is done
Preparing Lang class...
0.013073848567479729 % vocabulary building is done
Preparing Lang class...
0.014941541219981591 % vocabulary building is done
Preparing Lang class...
0.01680923387247235 % vocabulary building is done
Preparing Lang class...
0.018676926524974213 % vocabulary building is done
Preparing Lang class...
0.020544619177464973 % vocabulary building is done
Preparing Lang class...
0.022412311829966836 % vocabulary building is done
Preparing Lang class...
0.024280004482457596 % vocabulary building is don

1.0440401927458764 % vocabulary building is done
Preparing Lang class...
1.0459078853983783 % vocabulary building is done
Preparing Lang class...
1.0477755780508802 % vocabulary building is done
Preparing Lang class...
1.049643270703371 % vocabulary building is done
Preparing Lang class...
1.0515109633558728 % vocabulary building is done
Preparing Lang class...
1.0533786560083636 % vocabulary building is done
Preparing Lang class...
1.0552463486608654 % vocabulary building is done
Preparing Lang class...
1.0571140413133562 % vocabulary building is done
Preparing Lang class...
1.058981733965858 % vocabulary building is done
Preparing Lang class...
1.06084942661836 % vocabulary building is done
Preparing Lang class...
1.0627171192708507 % vocabulary building is done
Preparing Lang class...
1.0645848119233525 % vocabulary building is done
Preparing Lang class...
1.0664525045758433 % vocabulary building is done
Preparing Lang class...
1.0683201972283451 % vocabulary building is done
Prepar

2.560606626573536 % vocabulary building is done
Preparing Lang class...
2.562474319226027 % vocabulary building is done
Preparing Lang class...
2.5643420118785287 % vocabulary building is done
Preparing Lang class...
2.5662097045310195 % vocabulary building is done
Preparing Lang class...
2.5680773971835213 % vocabulary building is done
Preparing Lang class...
2.569945089836012 % vocabulary building is done
Preparing Lang class...
2.571812782488514 % vocabulary building is done
Preparing Lang class...
2.573680475141016 % vocabulary building is done
Preparing Lang class...
2.5755481677935066 % vocabulary building is done
Preparing Lang class...
2.5774158604460085 % vocabulary building is done
Preparing Lang class...
2.579283553098499 % vocabulary building is done
Preparing Lang class...
2.581151245751001 % vocabulary building is done
Preparing Lang class...
2.583018938403492 % vocabulary building is done
Preparing Lang class...
2.5848866310559937 % vocabulary building is done
Preparing 

3.785813006611627 % vocabulary building is done
Preparing Lang class...
3.7876806992641288 % vocabulary building is done
Preparing Lang class...
3.7895483919166306 % vocabulary building is done
Preparing Lang class...
3.7914160845691214 % vocabulary building is done
Preparing Lang class...
3.7932837772216232 % vocabulary building is done
Preparing Lang class...
3.795151469874114 % vocabulary building is done
Preparing Lang class...
3.797019162526616 % vocabulary building is done
Preparing Lang class...
3.7988868551791066 % vocabulary building is done
Preparing Lang class...
3.8007545478316085 % vocabulary building is done
Preparing Lang class...
3.8026222404841103 % vocabulary building is done
Preparing Lang class...
3.804489933136601 % vocabulary building is done
Preparing Lang class...
3.806357625789103 % vocabulary building is done
Preparing Lang class...
3.8082253184415937 % vocabulary building is done
Preparing Lang class...
3.8100930110940956 % vocabulary building is done
Prepari

5.1174778678420685 % vocabulary building is done
Preparing Lang class...
5.119345560494571 % vocabulary building is done
Preparing Lang class...
5.1212132531470616 % vocabulary building is done
Preparing Lang class...
5.123080945799563 % vocabulary building is done
Preparing Lang class...
5.124948638452054 % vocabulary building is done
Preparing Lang class...
5.126816331104555 % vocabulary building is done
Preparing Lang class...
5.128684023757046 % vocabulary building is done
Preparing Lang class...
5.130551716409548 % vocabulary building is done
Preparing Lang class...
5.1324194090620505 % vocabulary building is done
Preparing Lang class...
5.134287101714541 % vocabulary building is done
Preparing Lang class...
5.136154794367043 % vocabulary building is done
Preparing Lang class...
5.1380224870195335 % vocabulary building is done
Preparing Lang class...
5.139890179672035 % vocabulary building is done
Preparing Lang class...
5.141757872324526 % vocabulary building is done
Preparing La

...

93.875835792462 % vocabulary building is done
Preparing Lang class...
93.8777034851145 % vocabulary building is done
Preparing Lang class...
93.87957117776699 % vocabulary building is done
Preparing Lang class...
93.88143887041949 % vocabulary building is done
Preparing Lang class...
93.88330656307198 % vocabulary building is done
Preparing Lang class...
93.88517425572448 % vocabulary building is done
Preparing Lang class...
93.88704194837698 % vocabulary building is done
Preparing Lang class...
93.88890964102947 % vocabulary building is done
Preparing Lang class...
93.89077733368197 % vocabulary building is done
Preparing Lang class...
93.89264502633446 % vocabulary building is done
Preparing Lang class...
93.89451271898696 % vocabulary building is done
Preparing Lang class...
93.89638041163946 % vocabulary building is done
Preparing Lang class...
93.89824810429197 % vocabulary building is done
Preparing Lang class...
93.90011579694445 % vocabulary building is done
Preparing Lang clas

95.27286989652983 % vocabulary building is done
Preparing Lang class...
95.27473758918232 % vocabulary building is done
Preparing Lang class...
95.27660528183482 % vocabulary building is done
Preparing Lang class...
95.27847297448731 % vocabulary building is done
Preparing Lang class...
95.28034066713982 % vocabulary building is done
Preparing Lang class...
95.2822083597923 % vocabulary building is done
Preparing Lang class...
95.28407605244482 % vocabulary building is done
Preparing Lang class...
95.28594374509731 % vocabulary building is done
Preparing Lang class...
95.28781143774981 % vocabulary building is done
Preparing Lang class...
95.2896791304023 % vocabulary building is done
Preparing Lang class...
95.2915468230548 % vocabulary building is done
Preparing Lang class...
95.2934145157073 % vocabulary building is done
Preparing Lang class...
95.2952822083598 % vocabulary building is done
Preparing Lang class...
95.29714990101229 % vocabulary building is done
Preparing Lang class.

96.47566396473796 % vocabulary building is done
Preparing Lang class...
96.47753165739046 % vocabulary building is done
Preparing Lang class...
96.47939935004295 % vocabulary building is done
Preparing Lang class...
96.48126704269545 % vocabulary building is done
Preparing Lang class...
96.48313473534796 % vocabulary building is done
Preparing Lang class...
96.48500242800044 % vocabulary building is done
Preparing Lang class...
96.48687012065295 % vocabulary building is done
Preparing Lang class...
96.48873781330545 % vocabulary building is done
Preparing Lang class...
96.49060550595794 % vocabulary building is done
Preparing Lang class...
96.49247319861044 % vocabulary building is done
Preparing Lang class...
96.49434089126294 % vocabulary building is done
Preparing Lang class...
96.49620858391543 % vocabulary building is done
Preparing Lang class...
96.49807627656793 % vocabulary building is done
Preparing Lang class...
96.49994396922042 % vocabulary building is done
Preparing Lang c

Preparing Lang class...
97.90258115124576 % vocabulary building is done
Preparing Lang class...
97.90444884389825 % vocabulary building is done
Preparing Lang class...
97.90631653655075 % vocabulary building is done
Preparing Lang class...
97.90818422920324 % vocabulary building is done
Preparing Lang class...
97.91005192185574 % vocabulary building is done
Preparing Lang class...
97.91191961450824 % vocabulary building is done
Preparing Lang class...
97.91378730716073 % vocabulary building is done
Preparing Lang class...
97.91565499981323 % vocabulary building is done
Preparing Lang class...
97.91752269246572 % vocabulary building is done
Preparing Lang class...
97.91939038511822 % vocabulary building is done
Preparing Lang class...
97.92125807777072 % vocabulary building is done
Preparing Lang class...
97.92312577042321 % vocabulary building is done
Preparing Lang class...
97.92499346307572 % vocabulary building is done
Preparing Lang class...
97.92686115572822 % vocabulary building 

99.24358447573867 % vocabulary building is done
Preparing Lang class...
99.24545216839117 % vocabulary building is done
Preparing Lang class...
99.24731986104366 % vocabulary building is done
Preparing Lang class...
99.24918755369616 % vocabulary building is done
Preparing Lang class...
99.25105524634866 % vocabulary building is done
Preparing Lang class...
99.25292293900115 % vocabulary building is done
Preparing Lang class...
99.25479063165366 % vocabulary building is done
Preparing Lang class...
99.25665832430616 % vocabulary building is done
Preparing Lang class...
99.25852601695865 % vocabulary building is done
Preparing Lang class...
99.26039370961115 % vocabulary building is done
Preparing Lang class...
99.26226140226365 % vocabulary building is done
Preparing Lang class...
99.26412909491614 % vocabulary building is done
Preparing Lang class...
99.26599678756864 % vocabulary building is done
Preparing Lang class...
99.26786448022114 % vocabulary building is done
Preparing Lang c

In [ ]:
training_chunk_num = 42842

while training_chunk_num:
    try:
        # Read the pickle manually, to keep track of the stream
        print("Loading...")
        pairs = pickle.load(file_stream)
        random.shuffle(pairs)  

        # Load the previous states if its already initialized
        if initialized:            
            # To show progress, we can evaluate each step with the next chunk before using
            # it on training
            to_be_evaluated=[[],[]]

            for pair in pairs:
                to_be_evaluated[0].append(evaluate(encoder1, attndecoder1, pair[0]))
                to_be_evaluated[1].append(pair[1].split(' '))
                
            for i in range(min(len(to_be_evaluated[0]), 3)):
                print((to_be_evaluated[0][i], to_be_evaluated[1][i]))

            print(bleu_text(to_be_evaluated[0], to_be_evaluated[1]))
        else:
            initialized = True

        # This actually trains the model. The good part about this is that you can interrupt or stop it for a bit, and run it again
        # later, to continue the same training.
        print("Training...")
        trainIters(encoder1, attndecoder1, pairs, (len(pairs)//10), print_every=1)
        
        # To save the model in each iteration
        print("Saving...")
        torch.save(encoder1.state_dict(), f'models{folder_separator}model1encoder_state.pt')
        torch.save(attndecoder1.state_dict(), f'models{folder_separator}model1attn_decoder_state.pt')
        
        chunk_size_file = open(f'models{folder_separator}current_chunk.txt', 'w')
        chunk_size_file.write(str(training_chunk_num))
        chunk_size_file.close()
        
        print(f'{(1-(training_chunk_num/42842)) *100} % training is done')
        
        training_chunk_num -= 1
    # This exception shows when the set is not divided to the exact number of expected chunks
    except EOFError:
        raise Exception("You have reached the end of chunks")

In [25]:
pickle_off = f"data{folder_separator}final_sample.pkl"
file_stream = (open(pickle_off, "rb"))
file_stream.close()
lang_chunk_num = 53542
test_chunk_num = 10700
file_stream = (open(pickle_off, "rb"))
encoder1 = torch.load(f'models{folder_separator}model1encoder.pt')
attndecoder1 = torch.load(f'models{folder_separator}model1attn_decoder.pt')
to_be_evaluated=[[],[]]

while test_chunk_num:
    if lang_chunk_num > test_chunk_num:
        lang_chunk_num -= 1
        continue
    try:
        print("Testing chunk...")
        pairs = pickle.load(file_stream)

        for pair in pairs:
            to_be_evaluated[0].append(pair[1].split(' '))
            to_be_evaluated[1].append(evaluate(encoder1, attndecoder1, pair[0]))
            
        for i in range(min(len(to_be_evaluated[0]), 3)):
            print((to_be_evaluated[0][i], to_be_evaluated[1][i]))
            
        print(f'{(1-(test_chunk_num/10700)) *100} % testing is done')
        
        test_chunk_num -= 1
    except EOFError:
        raise Exception("You have reached the end of chunks")

Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
0.0 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
0.009345794392523477 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
0.018691588785046953 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'heb

(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
0.2429906542056104 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
0.25233644859813387 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
0.26168224299065734 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben'

(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
0.4859813084112097 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
0.49532710280373315 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
0.5046728971962566 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben',

(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
0.7383177570093435 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
0.747663551401867 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
0.7570093457943905 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', '

(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
0.9813084112149539 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
0.9906542056074774 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
1.0000000000000009 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 

...

(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
99.00934579439252 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
99.01869158878505 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
99.02803738317758 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'he

(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
99.25233644859813 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
99.26168224299066 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
99.27102803738318 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'he

(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
99.49532710280374 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
99.50467289719627 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
99.51401869158879 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'he

(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
99.73831775700934 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
99.74766355140187 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
99.75700934579439 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'he

(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
99.98130841121495 % testing is done
Testing chunk...
(['we', 'staan', 'erop'], ['we', 'hebben', 'het', 'het', '<EOS>'])
(['dit', 'hadden', 'we', 'niet', 'verwacht'], ['we', 'zijn', 'de', 'het', 'om', 'te', '<EOS>'])
(['oorspronkelijk', 'was', 'het', 'een', 'steen'], ['we', 'hebben', 'hier', 'hier', 'hier', '<EOS>'])
99.99065420560747 % testing is done


In [26]:
print(bleu_text(to_be_evaluated[0], to_be_evaluated[1], n_precision = 4))
print(bleu_text(to_be_evaluated[0], to_be_evaluated[1], n_precision = 3))
print(bleu_text(to_be_evaluated[0], to_be_evaluated[1], n_precision = 2))
print(bleu_text(to_be_evaluated[0], to_be_evaluated[1], n_precision = 1))

0.03148894864278529
0.09059534452818443
0.17008306249349162
0.2884916291497198
